## Gathering Training Data

So, I scrounged the internet for a database of Simpsons scripts, to no avail. I did find an archive of episode summaries though, and scraped the website to compile an admittedly flimsy data set.

Obviously, more comprehensive and better quality data would have been ideal. Even so, our flimsy dataset still managed to produce compelling results, which is a testament to the power of algorithms like GPT. 

In [ ]:
import requests

from bs4 import BeautifulSoup

In [2]:

from bs4 import BeautifulSoup

In [6]:
page = requests.get('https://www.simpsonsarchive.com/episodes.html')

soup = BeautifulSoup(page.content, "html.parser")

In [8]:
elements = soup.find_all("a")

In [43]:
index_list = [e.text for e in elements][92:389]

In [11]:
def get_episode(index_key):
    page = requests.get(f'https://www.simpsonsarchive.com/episodes/{index_key}.html')
    soup = BeautifulSoup(page.content, "html.parser")
    return soup.find_all('pre')

In [28]:
from tqdm import tqdm

def get_episodes(index_list):    
    results = []
    for idx in tqdm(index_list):
        results.append(get_episode(idx))
    return results

In [44]:
simpsons_data = get_episodes(index_list)

100%|██████████| 297/297 [01:16<00:00,  3.86it/s]


In [52]:
# simpsons_data[2].find_all('h1')[0].text

In [238]:
import re
def create_scripts_data(data):
    titles = []
    for script in data:
        # print(script.find_all('title')[0].text)
        title = script.find_all('title')
       
        moo = re.split('Quotes and scene summary',str(script),flags=re.IGNORECASE | re.DOTALL)##[1]
        if len(moo) > 1:
            text = 'EPISODE SUMMARY: ' + re.sub('<[^<]+?>', '', moo[1])
            if len(title) >= 1:
                pattern = r'\[.*?\]'
                title = re.sub(pattern, '', title[0].text.strip())
                title = title.strip()
                text = re.sub(title,'',text,flags=re.IGNORECASE)
                print(title)
                print(text)
                title = 'EPISODE TITLE: ' + title
 
        else:
            text = None
            title = None
       
        titles.append([title,text])
    return titles

In [239]:
complete_scripts = create_scripts_data(simpsons_data)

Simpsons Roasting on an Open Fire
EPISODE SUMMARY: 



 Homer and Marge drive to Springfield Elementary, late for the school's
 Christmas show.  A class sings ``O Little Town of Bethlehem'' as Marge
 (carrying Maggie, all bundled up) and Homer try to reach their seats.
 Next up is the second grade, presenting, ``Santas of many lands.''  After
 the German and Japanese versions of Santa Claus comes Lisa as Towanga,
 the Santa Claus of the South Seas.  Lisa appears, wearing a witch doctor
 mask and grass skirt, juggling flaming torches.

   Ah, the fourth grade will now favor us with a melody... err...
   medley (hee hee) of holiday flavorites.
   -- Principal Skinhead, err, Skinner hosts the school Christmas show,
      ``''

 They sing Jingle Bells, but Bart chooses some
 alternate lyrics.  He's yanked off the stage.  Time passes...

   Skinner: The fifth grade will now favor us with a scene from Charles
            uh.. Dickens' Christmas Carol.
   Homer:   Ohhhh.... How many grades do

In [240]:
def compile_scripts(complete_scripts):

    text_document = []

    for x in complete_scripts:
        
        if (x[0] != None) & (x[1] != None):
            if ('EPISODE TITLE' in x[0]) & ('404' not in x[0]):
                text_document.append(("\n\n\n").join([x[0],x[1].split('Contributors')[0]]))


    return (' ').join(text_document)

In [241]:
text_doc = compile_scripts(complete_scripts)
text_doc = text_doc.replace('',' ')

with open('../training_data/simpsons.txt', 'w') as f:
    f.write(text_doc)